In [1]:
# Import all packages used
import pandas as pd
import numpy as np
import spacy as sp
import string
import en_core_web_sm
import nltk as nl
import re

from sklearn.model_selection import train_test_split
from sklearn.metrics import precision_recall_fscore_support as score
from sklearn.feature_extraction.text import CountVectorizer
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.metrics import confusion_matrix
from sklearn.model_selection import GridSearchCV

from sklearn import svm

from sklearn.ensemble import RandomForestClassifier


from sklearn.naive_bayes import BernoulliNB

model = svm.SVC()
param = {'kernel': ['linear','rbf']}

lemm_obj = sp.load('en_core_web_lg')
lemm_obj.max_length = 1500000
ps = nl.PorterStemmer()

vect_cnt = CountVectorizer(analyzer='word',min_df=1,stop_words='english',token_pattern='[a-zA-Z0-9]{1,}')
tfidf_vect = TfidfVectorizer(analyzer = 'word', min_df = 1, stop_words = 'english',vocabulary=20000, token_pattern = '[a-zA-Z0-9]{1,}')

allowed_postags = ['NOUN','ADJ','VERB','ADV']

import pandas as pd
from collections import deque
import random
import numpy as np
import tensorflow as tf
from keras.models import Sequential, Model
from keras.layers import Dense, Dropout, LSTM, CuDNNLSTM, BatchNormalization, Embedding
from keras.preprocessing.text import Tokenizer
from keras.preprocessing.sequence import pad_sequences
import time
from sklearn import preprocessing
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import LabelEncoder
from keras.models import Model
from keras.optimizers import RMSprop
from keras.preprocessing.text import Tokenizer
from keras.preprocessing import sequence
from keras.utils import to_categorical
from keras.callbacks import EarlyStopping
from keras.wrappers.scikit_learn import KerasClassifier
from kerastuner import RandomSearch
from kerastuner.engine.hyperparameters import HyperParameters
import IPython

C:\Users\ragha\Anaconda3\lib\site-packages\tensorflow\python\framework\dtypes.py:516: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_qint8 = np.dtype([("qint8", np.int8, 1)])
C:\Users\ragha\Anaconda3\lib\site-packages\tensorflow\python\framework\dtypes.py:517: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_quint8 = np.dtype([("quint8", np.uint8, 1)])
C:\Users\ragha\Anaconda3\lib\site-packages\tensorflow\python\framework\dtypes.py:518: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_qint16 = np.dtype([("qint16", np.int16, 1)])
C:\Users\ragha\Anaconda3\lib\site-packages\tensorflow\python\framework\dtypes.py:519: FutureWarning: Passi

In [2]:
gen_df_encode = pd.read_pickle("D:\Machine Learning\Vamsi Thesis\Code\Results\gen_df_encode.pkl")

In [3]:
fullMovieData = pd.read_pickle(r"D:\Machine Learning\Vamsi Thesis\Code\Results\fullMovieData.pkl")
# List of genres
g_list = fullMovieData.apply(lambda x: x['genres'].split('|'),axis = 1)
g_list=g_list.to_list()
g_list=list(set(sum(g_list,[])))
g_list

['Comedy',
 'IMAX',
 'War',
 'Thriller',
 'Horror',
 'Crime',
 'Mystery',
 'Action',
 'Film-Noir',
 'Drama',
 'Sci-Fi',
 'Documentary',
 'Musical',
 'Romance',
 'Western',
 'Fantasy',
 'Animation',
 'Adventure',
 'Children']

In [4]:
# Application of RNN - LSTM
Final_data=pd.DataFrame(columns=["Genre","Actual Negatives","Actual Positives","Vectorizer","Model","Test_Precision","Test_Recall","Test_Fscore","Precision","Recall","Fscore"])
Final_data.shape
def rnn_prediction(df,text,genre,param):
    result=[]
    print("Genre for prediction: ", genre)
    result.append(genre)
    
    #Sampling
    df_model_0 = df[df[genre] == 0]
    df_model_1 = df[df[genre] == 1]
    print("Number of 0s: ", df_model_0.shape[0])
    print("Number of 1s: ", df_model_1.shape[0])
    result.append(df_model_0.shape[0])
    result.append(df_model_1.shape[0]) 
    
    sample_size = 2*df_model_1.shape[0]
    if sample_size > len(df_model_0) : sample_size = len(df_model_0)
    df_model_s=pd.concat([df_model_1,df_model_0.sample(sample_size)])
    print("Shape of the Sampled DataFrame: ", df_model_s.shape)
    #result.append(df_model_s.shape[0])
    
    #Train-Test Split
    X_df = df_model_s[text]
    y_df = df_model_s[genre]
    X_train,X_test,y_train,y_test = train_test_split(X_df, y_df, test_size = 0.10, random_state = 1,
                                                     shuffle = True)

    vocab = 10000
    max_len = 12
    print("\n")
    result.append("LSTM Sequence Padding")
    result.append("LSTM RNN")
    print("Vectorization Start")
    tok = Tokenizer(num_words=vocab)
    tok.fit_on_texts(X_train)
    sequences = tok.texts_to_sequences(X_train)
    sequences_matrix = sequence.pad_sequences(sequences,maxlen=max_len)
    test_sequences = tok.texts_to_sequences(X_test)
    test_sequences_matrix = sequence.pad_sequences(test_sequences,maxlen=max_len)
    print("Vectorization End")
    print("\n")
    
    print("Recurrent Neural Networks building started")
    embedding_vector_length = 32
    def model_dec():
        model = Sequential()
        model.add(Embedding(vocab, embedding_vector_length, input_length=max_len))
        model.add(LSTM(500))
        model.add(Dropout(0.3))
        model.add(Dense(1, activation='sigmoid'))
        model.compile(loss='binary_crossentropy', optimizer='adam', metrics=['accuracy'])
        return model
    model = model_dec()
    print(model.summary())
    print("Recurrent Neural Networks Gridsearch starts")    
    
    epoch=list(param.values())[0]
    batch_size = list(param.values())[1]
    scores=[]
    optimal_epoch=0
    optimal_batch=0
    for i in epoch:
        for j in batch_size:
            model.fit(sequences_matrix, y_train, validation_data=(test_sequences_matrix, y_test), epochs=i, batch_size=j)
            # Final evaluation of the model
            scores.append(model.evaluate(test_sequences_matrix, y_test, verbose=0)[1])
            if len(scores)>1:
                max_score = max(scores)
                if scores[len(scores)-1]==max_score:
                    optimal_epoch=i
                    optimal_batch=j

    print("Optimal epoch:%i" % optimal_epoch)
    print("Optimal batch:%i" % optimal_batch)
    
    
    # Predicting test set
    model.fit(sequences_matrix, y_train, epochs=optimal_epoch, batch_size=optimal_batch)        
    scores = model.evaluate(test_sequences_matrix, y_test, verbose=0)
    test_pred_cnt=model.predict_classes(test_sequences_matrix)
    test_pred_prob=model.predict(test_sequences_matrix)
    print("\n")
    print("Test Accuracy: %.2f%%" % (scores[1]*100))
    print("Sample data Test Set Confusion Matrix: ")  
    print(confusion_matrix(y_test, test_pred_cnt))
    precision, recall, fscore, train_support = score(y_test, test_pred_cnt, pos_label = 1, average = 'binary')
    print("Sample data Test Set Precision: ", precision)
    print("Sample data Test Set Recall: ", recall)
    print("Sample data Test Set FScore: ", fscore)
    print("\n")   
    result.extend([precision, recall, fscore])

    
    # Prediction on train set
    scores = model.evaluate(sequences_matrix, y_train, verbose=0)
    train_pred_cnt=model.predict_classes(sequences_matrix)
    
    # Train Accuracy
    print("Sample data Train Set Confusion Matrix: ")
    print("Train Accuracy: %.2f%%" % (scores[1]*100))
    print(confusion_matrix(y_train, train_pred_cnt))
    precision, recall, fscore, train_support = score(y_train, train_pred_cnt, pos_label = 1, average = 'binary')
    print("Sample data Train Set (Precision, Recall, Fscore) :", precision, recall, fscore)
    print("\n")
    
    
    
    #Accuracy on full Data
    X_df_full = df[text]
    y_df_full = df[genre]

    # Tokenization 
    
    full_sequences = tok.texts_to_sequences(X_df_full)
    X_full_tf = sequence.pad_sequences(full_sequences,maxlen=max_len)
    
    
    print("Probability Evaluation and Concat Start")
    full_pred_cnt = pd.DataFrame(model.predict_classes(X_full_tf))
    full_pred_prob = pd.DataFrame(model.predict(X_full_tf))
    print(full_pred_prob)
    df = pd.concat([df,full_pred_prob], axis = 1)
    
    df.rename(columns ={0:genre+'_prob'},inplace=True)
#     df.drop([0],axis=1,inplace=True)
    print("Probability Evaluation and Concat End")
    
    print("\n")
    print("Full Dataset Confusion Matrix ")
    print(confusion_matrix(y_df_full, full_pred_cnt))
    precision, recall, fscore, train_support = score(y_df_full, full_pred_cnt, pos_label = 1, average = 'binary')
    print("Full Dataset Precision: ", precision)
    print("Full Dataset Recall: ", recall)
    print("Full Dataset FScore: ", fscore)
    print("\n")
    result.extend([precision, recall, fscore])
    
    df.dropna(inplace=True)
    
    print("Appending results to Final_data Start")
    Final_data.loc[len(Final_data)]=result
    print("Appending results to Final_data End")
        
    return df

In [7]:
start = time.time()
df_test=gen_df_encode
for i in g_list:    
    df_test = rnn_prediction(df_test,'plot_lemm',i,{'epoch':[5,8,10],'batch':[50,100,500,1000]})
df_test.to_pickle(r'D:\Machine Learning\Vamsi Thesis\Code\Results\LSTM_Probability_Distribution_plots.pkl')
Final_data.to_pickle(r'D:\Machine Learning\Vamsi Thesis\Code\Results\Result_LSTM_plot.pkl')
end = time.time()
total_time = end-start

print("Total Time taken:" + str(end-start))

Genre for prediction:  Comedy
Number of 0s:  6914
Number of 1s:  3488
Shape of the Sampled DataFrame:  (10402, 29)


Vectorization Start
Vectorization End


Recurrent Neural Networks building started
Model: "sequential_20"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
embedding_20 (Embedding)     (None, 12, 32)            320000    
_________________________________________________________________
lstm_20 (LSTM)               (None, 500)               1066000   
_________________________________________________________________
dropout_20 (Dropout)         (None, 500)               0         
_________________________________________________________________
dense_20 (Dense)             (None, 1)                 501       
Total params: 1,386,501
Trainable params: 1,386,501
Non-trainable params: 0
_________________________________________________________________
None
Recurrent Neural Networks Gridsearch

9361/9361 [==============================] - ETA: 17s - loss: 0.5632 - accuracy: 0.700 - ETA: 17s - loss: 0.5854 - accuracy: 0.650 - ETA: 17s - loss: 0.5652 - accuracy: 0.686 - ETA: 17s - loss: 0.5578 - accuracy: 0.715 - ETA: 17s - loss: 0.5588 - accuracy: 0.720 - ETA: 17s - loss: 0.5518 - accuracy: 0.726 - ETA: 17s - loss: 0.5484 - accuracy: 0.734 - ETA: 17s - loss: 0.5334 - accuracy: 0.750 - ETA: 17s - loss: 0.5356 - accuracy: 0.742 - ETA: 16s - loss: 0.5326 - accuracy: 0.738 - ETA: 16s - loss: 0.5221 - accuracy: 0.741 - ETA: 16s - loss: 0.5362 - accuracy: 0.725 - ETA: 16s - loss: 0.5376 - accuracy: 0.724 - ETA: 16s - loss: 0.5314 - accuracy: 0.728 - ETA: 16s - loss: 0.5248 - accuracy: 0.732 - ETA: 16s - loss: 0.5213 - accuracy: 0.730 - ETA: 16s - loss: 0.5219 - accuracy: 0.729 - ETA: 16s - loss: 0.5183 - accuracy: 0.732 - ETA: 16s - loss: 0.5155 - accuracy: 0.734 - ETA: 15s - loss: 0.5137 - accuracy: 0.737 - ETA: 15s - loss: 0.5174 - accuracy: 0.739 - ETA: 15s - loss: 0.5121 - accur

9361/9361 [==============================] - ETA: 13s - loss: 0.4264 - accuracy: 0.740 - ETA: 13s - loss: 0.3784 - accuracy: 0.830 - ETA: 13s - loss: 0.3685 - accuracy: 0.846 - ETA: 13s - loss: 0.3779 - accuracy: 0.860 - ETA: 13s - loss: 0.3684 - accuracy: 0.860 - ETA: 13s - loss: 0.3548 - accuracy: 0.866 - ETA: 13s - loss: 0.3396 - accuracy: 0.871 - ETA: 13s - loss: 0.3352 - accuracy: 0.867 - ETA: 13s - loss: 0.3416 - accuracy: 0.864 - ETA: 12s - loss: 0.3428 - accuracy: 0.858 - ETA: 12s - loss: 0.3329 - accuracy: 0.863 - ETA: 12s - loss: 0.3368 - accuracy: 0.861 - ETA: 12s - loss: 0.3376 - accuracy: 0.861 - ETA: 12s - loss: 0.3353 - accuracy: 0.861 - ETA: 12s - loss: 0.3352 - accuracy: 0.860 - ETA: 12s - loss: 0.3317 - accuracy: 0.862 - ETA: 12s - loss: 0.3303 - accuracy: 0.862 - ETA: 12s - loss: 0.3245 - accuracy: 0.866 - ETA: 12s - loss: 0.3221 - accuracy: 0.866 - ETA: 12s - loss: 0.3174 - accuracy: 0.869 - ETA: 12s - loss: 0.3270 - accuracy: 0.863 - ETA: 11s - loss: 0.3285 - accur

9361/9361 [==============================] - ETA: 8s - loss: 0.1375 - accuracy: 0.97 - ETA: 8s - loss: 0.1844 - accuracy: 0.93 - ETA: 8s - loss: 0.1764 - accuracy: 0.94 - ETA: 8s - loss: 0.1954 - accuracy: 0.94 - ETA: 8s - loss: 0.2034 - accuracy: 0.93 - ETA: 7s - loss: 0.1993 - accuracy: 0.93 - ETA: 7s - loss: 0.1933 - accuracy: 0.93 - ETA: 7s - loss: 0.1921 - accuracy: 0.93 - ETA: 7s - loss: 0.1865 - accuracy: 0.93 - ETA: 7s - loss: 0.1878 - accuracy: 0.93 - ETA: 7s - loss: 0.1829 - accuracy: 0.93 - ETA: 7s - loss: 0.1834 - accuracy: 0.93 - ETA: 7s - loss: 0.1885 - accuracy: 0.93 - ETA: 6s - loss: 0.1829 - accuracy: 0.94 - ETA: 6s - loss: 0.1829 - accuracy: 0.93 - ETA: 6s - loss: 0.1813 - accuracy: 0.94 - ETA: 6s - loss: 0.1807 - accuracy: 0.94 - ETA: 6s - loss: 0.1769 - accuracy: 0.94 - ETA: 6s - loss: 0.1748 - accuracy: 0.94 - ETA: 6s - loss: 0.1767 - accuracy: 0.94 - ETA: 6s - loss: 0.1737 - accuracy: 0.94 - ETA: 6s - loss: 0.1730 - accuracy: 0.94 - ETA: 6s - loss: 0.1759 - accura

9361/9361 [==============================] - ETA: 7s - loss: 0.1086 - accuracy: 0.97 - ETA: 7s - loss: 0.0679 - accuracy: 0.98 - ETA: 7s - loss: 0.0969 - accuracy: 0.97 - ETA: 7s - loss: 0.0795 - accuracy: 0.98 - ETA: 7s - loss: 0.0789 - accuracy: 0.97 - ETA: 7s - loss: 0.0916 - accuracy: 0.97 - ETA: 7s - loss: 0.0863 - accuracy: 0.97 - ETA: 7s - loss: 0.0817 - accuracy: 0.98 - ETA: 7s - loss: 0.0771 - accuracy: 0.98 - ETA: 7s - loss: 0.0759 - accuracy: 0.98 - ETA: 6s - loss: 0.0736 - accuracy: 0.98 - ETA: 6s - loss: 0.0692 - accuracy: 0.98 - ETA: 6s - loss: 0.0678 - accuracy: 0.98 - ETA: 6s - loss: 0.0683 - accuracy: 0.98 - ETA: 6s - loss: 0.0652 - accuracy: 0.98 - ETA: 6s - loss: 0.0644 - accuracy: 0.98 - ETA: 6s - loss: 0.0640 - accuracy: 0.98 - ETA: 6s - loss: 0.0639 - accuracy: 0.98 - ETA: 6s - loss: 0.0645 - accuracy: 0.98 - ETA: 6s - loss: 0.0639 - accuracy: 0.98 - ETA: 6s - loss: 0.0642 - accuracy: 0.98 - ETA: 6s - loss: 0.0643 - accuracy: 0.98 - ETA: 5s - loss: 0.0636 - accura

...

Epoch 4/10
2392/2392 [==============================] - ETA: 1s - loss: 1.2520e-05 - accuracy: 1.00 - ETA: 0s - loss: 1.1764e-05 - accuracy: 1.00 - ETA: 0s - loss: 1.2175e-05 - accuracy: 1.00 - ETA: 0s - loss: 1.3641e-05 - accuracy: 1.00 - 1s 585us/step - loss: 1.2960e-05 - accuracy: 1.0000 - val_loss: 6.3983 - val_accuracy: 0.6579
Epoch 5/10
2392/2392 [==============================] - ETA: 1s - loss: 1.6730e-05 - accuracy: 1.00 - ETA: 0s - loss: 1.3060e-05 - accuracy: 1.00 - ETA: 0s - loss: 1.2878e-05 - accuracy: 1.00 - ETA: 0s - loss: 1.2733e-05 - accuracy: 1.00 - 1s 574us/step - loss: 1.2203e-05 - accuracy: 1.0000 - val_loss: 6.4027 - val_accuracy: 0.6579
Epoch 6/10
2392/2392 [==============================] - ETA: 1s - loss: 1.0233e-05 - accuracy: 1.00 - ETA: 0s - loss: 1.1456e-05 - accuracy: 1.00 - ETA: 0s - loss: 1.2341e-05 - accuracy: 1.00 - ETA: 0s - loss: 1.2345e-05 - accuracy: 1.00 - 1s 596us/step - loss: 1.1596e-05 - accuracy: 1.0000 - val_loss: 6.4072 - val_accuracy: 0.657

1398/1398 [==============================] - ETA: 1s - loss: 0.0107 - accuracy: 0.99 - ETA: 1s - loss: 0.0094 - accuracy: 0.99 - ETA: 1s - loss: 0.0185 - accuracy: 0.99 - ETA: 1s - loss: 0.0208 - accuracy: 0.99 - ETA: 0s - loss: 0.0172 - accuracy: 0.99 - ETA: 0s - loss: 0.0147 - accuracy: 0.99 - ETA: 0s - loss: 0.0198 - accuracy: 0.99 - ETA: 0s - loss: 0.0178 - accuracy: 0.99 - ETA: 0s - loss: 0.0161 - accuracy: 0.99 - ETA: 0s - loss: 0.0154 - accuracy: 0.99 - ETA: 0s - loss: 0.0148 - accuracy: 0.99 - ETA: 0s - loss: 0.0140 - accuracy: 0.99 - ETA: 0s - loss: 0.0137 - accuracy: 0.99 - 2s 1ms/step - loss: 0.0135 - accuracy: 0.9964 - val_loss: 1.6004 - val_accuracy: 0.6410
Epoch 4/5
1398/1398 [==============================] - ETA: 1s - loss: 0.0143 - accuracy: 0.99 - ETA: 1s - loss: 0.0084 - accuracy: 0.99 - ETA: 1s - loss: 0.0074 - accuracy: 0.99 - ETA: 1s - loss: 0.0121 - accuracy: 0.99 - ETA: 0s - loss: 0.0110 - accuracy: 0.99 - ETA: 0s - loss: 0.0096 - accuracy: 0.99 - ETA: 0s - loss

1398/1398 [==============================] - ETA: 1s - loss: 1.5900e-04 - accuracy: 1.00 - ETA: 1s - loss: 1.6372e-04 - accuracy: 1.00 - ETA: 1s - loss: 1.7628e-04 - accuracy: 1.00 - ETA: 1s - loss: 0.0021 - accuracy: 0.9975   - ETA: 0s - loss: 0.0017 - accuracy: 0.99 - ETA: 0s - loss: 0.0014 - accuracy: 0.99 - ETA: 0s - loss: 0.0013 - accuracy: 0.99 - ETA: 0s - loss: 0.0011 - accuracy: 0.99 - ETA: 0s - loss: 0.0031 - accuracy: 0.99 - ETA: 0s - loss: 0.0028 - accuracy: 0.99 - ETA: 0s - loss: 0.0040 - accuracy: 0.99 - ETA: 0s - loss: 0.0043 - accuracy: 0.99 - ETA: 0s - loss: 0.0040 - accuracy: 0.99 - 2s 1ms/step - loss: 0.0037 - accuracy: 0.9971 - val_loss: 2.6462 - val_accuracy: 0.6923
Epoch 4/8
1398/1398 [==============================] - ETA: 1s - loss: 2.6973e-04 - accuracy: 1.00 - ETA: 1s - loss: 7.3347e-04 - accuracy: 1.00 - ETA: 1s - loss: 7.2215e-04 - accuracy: 1.00 - ETA: 1s - loss: 7.5349e-04 - accuracy: 1.00 - ETA: 0s - loss: 6.9296e-04 - accuracy: 1.00 - ETA: 0s - loss: 6.10

1398/1398 [==============================] - ETA: 2s - loss: 1.0341e-04 - accuracy: 1.00 - ETA: 2s - loss: 5.5467e-04 - accuracy: 1.00 - ETA: 2s - loss: 7.4787e-04 - accuracy: 1.00 - ETA: 2s - loss: 0.0210 - accuracy: 0.9950   - ETA: 2s - loss: 0.0429 - accuracy: 0.99 - ETA: 2s - loss: 0.0359 - accuracy: 0.99 - ETA: 1s - loss: 0.0316 - accuracy: 0.99 - ETA: 1s - loss: 0.0323 - accuracy: 0.99 - ETA: 1s - loss: 0.0328 - accuracy: 0.99 - ETA: 1s - loss: 0.0370 - accuracy: 0.99 - ETA: 1s - loss: 0.0382 - accuracy: 0.99 - ETA: 1s - loss: 0.0409 - accuracy: 0.99 - ETA: 1s - loss: 0.0403 - accuracy: 0.99 - ETA: 1s - loss: 0.0378 - accuracy: 0.99 - ETA: 1s - loss: 0.0361 - accuracy: 0.99 - ETA: 1s - loss: 0.0339 - accuracy: 0.99 - ETA: 1s - loss: 0.0320 - accuracy: 0.99 - ETA: 0s - loss: 0.0302 - accuracy: 0.99 - ETA: 0s - loss: 0.0356 - accuracy: 0.99 - ETA: 0s - loss: 0.0339 - accuracy: 0.99 - ETA: 0s - loss: 0.0326 - accuracy: 0.99 - ETA: 0s - loss: 0.0313 - accuracy: 0.99 - ETA: 0s - loss:

Epoch 9/10
1398/1398 [==============================] - ETA: 0s - loss: 4.4832e-04 - accuracy: 1.00 - 1s 563us/step - loss: 0.0017 - accuracy: 0.9993 - val_loss: 3.0805 - val_accuracy: 0.6603
Epoch 10/10
1398/1398 [==============================] - ETA: 0s - loss: 0.0021 - accuracy: 0.99 - 1s 559us/step - loss: 0.0017 - accuracy: 0.9993 - val_loss: 3.0857 - val_accuracy: 0.6603
Optimal epoch:10
Optimal batch:50
Epoch 1/10
1398/1398 [==============================] - ETA: 2s - loss: 1.1611e-04 - accuracy: 1.00 - ETA: 2s - loss: 0.0163 - accuracy: 0.9900   - ETA: 2s - loss: 0.0109 - accuracy: 0.99 - ETA: 2s - loss: 0.0082 - accuracy: 0.99 - ETA: 2s - loss: 0.0066 - accuracy: 0.99 - ETA: 2s - loss: 0.0055 - accuracy: 0.99 - ETA: 1s - loss: 0.0047 - accuracy: 0.99 - ETA: 1s - loss: 0.0041 - accuracy: 0.99 - ETA: 1s - loss: 0.0037 - accuracy: 0.99 - ETA: 1s - loss: 0.0033 - accuracy: 0.99 - ETA: 1s - loss: 0.0030 - accuracy: 0.99 - ETA: 1s - loss: 0.0028 - accuracy: 0.99 - ETA: 1s - loss: 0

In [8]:
start = time.time()
df_test=gen_df_encode
for i in g_list:    
    df_test = rnn_prediction(df_test,'tt_lemm',i,{'epoch':[5,8,10],'batch':[50,100,500,1000]})
df_test.to_pickle(r'D:\Machine Learning\Vamsi Thesis\Code\Results\NB_Probability_Distribution_tt.pkl')
Final_data.to_pickle(r'D:\Machine Learning\Vamsi Thesis\Code\Results\Result_LSTM_tt.pkl')
end = time.time()
total_time = end-start

print("Total Time taken:" + str(end-start))

Genre for prediction:  Comedy
Number of 0s:  6914
Number of 1s:  3488
Shape of the Sampled DataFrame:  (10402, 29)


Vectorization Start
Vectorization End


Recurrent Neural Networks building started
Model: "sequential_39"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
embedding_39 (Embedding)     (None, 12, 32)            320000    
_________________________________________________________________
lstm_39 (LSTM)               (None, 500)               1066000   
_________________________________________________________________
dropout_39 (Dropout)         (None, 500)               0         
_________________________________________________________________
dense_39 (Dense)             (None, 1)                 501       
Total params: 1,386,501
Trainable params: 1,386,501
Non-trainable params: 0
_________________________________________________________________
None
Recurrent Neural Networks Gridsearch

9361/9361 [==============================] - ETA: 19s - loss: 0.5318 - accuracy: 0.740 - ETA: 19s - loss: 0.5387 - accuracy: 0.740 - ETA: 19s - loss: 0.5560 - accuracy: 0.713 - ETA: 19s - loss: 0.5687 - accuracy: 0.705 - ETA: 19s - loss: 0.5436 - accuracy: 0.728 - ETA: 19s - loss: 0.5255 - accuracy: 0.746 - ETA: 18s - loss: 0.5310 - accuracy: 0.745 - ETA: 18s - loss: 0.5459 - accuracy: 0.732 - ETA: 18s - loss: 0.5508 - accuracy: 0.728 - ETA: 18s - loss: 0.5511 - accuracy: 0.730 - ETA: 18s - loss: 0.5422 - accuracy: 0.740 - ETA: 17s - loss: 0.5403 - accuracy: 0.740 - ETA: 17s - loss: 0.5444 - accuracy: 0.733 - ETA: 17s - loss: 0.5443 - accuracy: 0.728 - ETA: 17s - loss: 0.5458 - accuracy: 0.724 - ETA: 17s - loss: 0.5511 - accuracy: 0.718 - ETA: 16s - loss: 0.5475 - accuracy: 0.721 - ETA: 16s - loss: 0.5525 - accuracy: 0.718 - ETA: 16s - loss: 0.5522 - accuracy: 0.720 - ETA: 16s - loss: 0.5489 - accuracy: 0.722 - ETA: 16s - loss: 0.5512 - accuracy: 0.718 - ETA: 16s - loss: 0.5476 - accur

9361/9361 [==============================] - ETA: 16s - loss: 0.4245 - accuracy: 0.860 - ETA: 16s - loss: 0.3976 - accuracy: 0.850 - ETA: 16s - loss: 0.3542 - accuracy: 0.866 - ETA: 16s - loss: 0.3643 - accuracy: 0.850 - ETA: 16s - loss: 0.3710 - accuracy: 0.848 - ETA: 16s - loss: 0.3664 - accuracy: 0.846 - ETA: 16s - loss: 0.3623 - accuracy: 0.842 - ETA: 16s - loss: 0.3661 - accuracy: 0.850 - ETA: 16s - loss: 0.3661 - accuracy: 0.853 - ETA: 16s - loss: 0.3755 - accuracy: 0.846 - ETA: 16s - loss: 0.3742 - accuracy: 0.841 - ETA: 16s - loss: 0.3766 - accuracy: 0.841 - ETA: 16s - loss: 0.3799 - accuracy: 0.835 - ETA: 15s - loss: 0.3822 - accuracy: 0.837 - ETA: 15s - loss: 0.3819 - accuracy: 0.838 - ETA: 15s - loss: 0.3783 - accuracy: 0.843 - ETA: 15s - loss: 0.3778 - accuracy: 0.842 - ETA: 15s - loss: 0.3800 - accuracy: 0.838 - ETA: 15s - loss: 0.3766 - accuracy: 0.840 - ETA: 15s - loss: 0.3817 - accuracy: 0.836 - ETA: 15s - loss: 0.3797 - accuracy: 0.837 - ETA: 15s - loss: 0.3807 - accur

Train on 9361 samples, validate on 1041 samples
Epoch 1/5
9361/9361 [==============================] - ETA: 10s - loss: 0.3238 - accuracy: 0.860 - ETA: 10s - loss: 0.2958 - accuracy: 0.880 - ETA: 10s - loss: 0.2836 - accuracy: 0.893 - ETA: 10s - loss: 0.2878 - accuracy: 0.895 - ETA: 10s - loss: 0.2810 - accuracy: 0.896 - ETA: 10s - loss: 0.2829 - accuracy: 0.888 - ETA: 10s - loss: 0.2708 - accuracy: 0.894 - ETA: 9s - loss: 0.2747 - accuracy: 0.891 - ETA: 9s - loss: 0.2810 - accuracy: 0.88 - ETA: 9s - loss: 0.2831 - accuracy: 0.88 - ETA: 9s - loss: 0.2845 - accuracy: 0.88 - ETA: 9s - loss: 0.2841 - accuracy: 0.88 - ETA: 9s - loss: 0.2809 - accuracy: 0.88 - ETA: 9s - loss: 0.2761 - accuracy: 0.88 - ETA: 8s - loss: 0.2821 - accuracy: 0.88 - ETA: 8s - loss: 0.2825 - accuracy: 0.88 - ETA: 8s - loss: 0.2813 - accuracy: 0.88 - ETA: 8s - loss: 0.2816 - accuracy: 0.88 - ETA: 8s - loss: 0.2826 - accuracy: 0.88 - ETA: 8s - loss: 0.2783 - accuracy: 0.88 - ETA: 8s - loss: 0.2766 - accuracy: 0.88 - 

9361/9361 [==============================] - ETA: 9s - loss: 0.1678 - accuracy: 0.94 - ETA: 9s - loss: 0.1930 - accuracy: 0.92 - ETA: 9s - loss: 0.1824 - accuracy: 0.92 - ETA: 9s - loss: 0.1681 - accuracy: 0.93 - ETA: 9s - loss: 0.1622 - accuracy: 0.93 - ETA: 9s - loss: 0.1615 - accuracy: 0.93 - ETA: 9s - loss: 0.1715 - accuracy: 0.93 - ETA: 9s - loss: 0.1702 - accuracy: 0.93 - ETA: 9s - loss: 0.1639 - accuracy: 0.93 - ETA: 9s - loss: 0.1623 - accuracy: 0.93 - ETA: 9s - loss: 0.1672 - accuracy: 0.93 - ETA: 8s - loss: 0.1684 - accuracy: 0.93 - ETA: 8s - loss: 0.1664 - accuracy: 0.93 - ETA: 8s - loss: 0.1675 - accuracy: 0.93 - ETA: 8s - loss: 0.1664 - accuracy: 0.93 - ETA: 8s - loss: 0.1674 - accuracy: 0.93 - ETA: 8s - loss: 0.1644 - accuracy: 0.93 - ETA: 8s - loss: 0.1670 - accuracy: 0.93 - ETA: 8s - loss: 0.1689 - accuracy: 0.92 - ETA: 7s - loss: 0.1701 - accuracy: 0.92 - ETA: 7s - loss: 0.1726 - accuracy: 0.92 - ETA: 7s - loss: 0.1744 - accuracy: 0.92 - ETA: 7s - loss: 0.1746 - accura

...

1398/1398 [==============================] - ETA: 4s - loss: 0.3082 - accuracy: 0.88 - ETA: 4s - loss: 0.3050 - accuracy: 0.86 - ETA: 4s - loss: 0.3789 - accuracy: 0.84 - ETA: 4s - loss: 0.3701 - accuracy: 0.84 - ETA: 4s - loss: 0.4111 - accuracy: 0.81 - ETA: 3s - loss: 0.4154 - accuracy: 0.80 - ETA: 3s - loss: 0.4119 - accuracy: 0.80 - ETA: 3s - loss: 0.4218 - accuracy: 0.80 - ETA: 3s - loss: 0.4212 - accuracy: 0.81 - ETA: 3s - loss: 0.4220 - accuracy: 0.82 - ETA: 3s - loss: 0.4196 - accuracy: 0.82 - ETA: 2s - loss: 0.4148 - accuracy: 0.82 - ETA: 2s - loss: 0.4110 - accuracy: 0.82 - ETA: 2s - loss: 0.4179 - accuracy: 0.82 - ETA: 2s - loss: 0.4296 - accuracy: 0.81 - ETA: 2s - loss: 0.4265 - accuracy: 0.82 - ETA: 2s - loss: 0.4203 - accuracy: 0.82 - ETA: 1s - loss: 0.4136 - accuracy: 0.83 - ETA: 1s - loss: 0.4106 - accuracy: 0.83 - ETA: 1s - loss: 0.4137 - accuracy: 0.82 - ETA: 1s - loss: 0.4132 - accuracy: 0.82 - ETA: 1s - loss: 0.4088 - accuracy: 0.83 - ETA: 0s - loss: 0.4077 - accura

Epoch 5/5
1398/1398 [==============================] - ETA: 0s - loss: 0.0219 - accuracy: 0.99 - ETA: 0s - loss: 0.0294 - accuracy: 0.99 - 1s 757us/step - loss: 0.0272 - accuracy: 0.9950 - val_loss: 2.1497 - val_accuracy: 0.6282
Train on 1398 samples, validate on 156 samples
Epoch 1/5
1398/1398 [==============================] - ETA: 0s - loss: 0.0227 - accuracy: 0.99 - 1s 708us/step - loss: 0.0230 - accuracy: 0.9950 - val_loss: 1.9716 - val_accuracy: 0.6154
Epoch 2/5
1398/1398 [==============================] - ETA: 0s - loss: 0.0224 - accuracy: 0.99 - 1s 688us/step - loss: 0.0211 - accuracy: 0.9971 - val_loss: 1.8930 - val_accuracy: 0.6154
Epoch 3/5
1398/1398 [==============================] - ETA: 0s - loss: 0.0209 - accuracy: 0.99 - 1s 681us/step - loss: 0.0194 - accuracy: 0.9986 - val_loss: 1.9143 - val_accuracy: 0.6154
Epoch 4/5
1398/1398 [==============================] - ETA: 0s - loss: 0.0188 - accuracy: 0.99 - 1s 683us/step - loss: 0.0180 - accuracy: 0.9979 - val_loss: 2.0277

1398/1398 [==============================] - ETA: 2s - loss: 5.4909e-04 - accuracy: 1.00 - ETA: 2s - loss: 5.7965e-04 - accuracy: 1.00 - ETA: 2s - loss: 0.0022 - accuracy: 1.0000   - ETA: 2s - loss: 0.0019 - accuracy: 1.00 - ETA: 1s - loss: 0.0017 - accuracy: 1.00 - ETA: 1s - loss: 0.0015 - accuracy: 1.00 - ETA: 1s - loss: 0.0013 - accuracy: 1.00 - ETA: 1s - loss: 0.0020 - accuracy: 1.00 - ETA: 1s - loss: 0.0022 - accuracy: 1.00 - ETA: 0s - loss: 0.0020 - accuracy: 1.00 - ETA: 0s - loss: 0.0019 - accuracy: 1.00 - ETA: 0s - loss: 0.0046 - accuracy: 0.99 - ETA: 0s - loss: 0.0047 - accuracy: 0.99 - 3s 2ms/step - loss: 0.0057 - accuracy: 0.9986 - val_loss: 2.8360 - val_accuracy: 0.6538
Epoch 8/8
1398/1398 [==============================] - ETA: 2s - loss: 5.9686e-04 - accuracy: 1.00 - ETA: 2s - loss: 6.8526e-04 - accuracy: 1.00 - ETA: 2s - loss: 5.8583e-04 - accuracy: 1.00 - ETA: 2s - loss: 0.0075 - accuracy: 0.9950   - ETA: 1s - loss: 0.0061 - accuracy: 0.99 - ETA: 1s - loss: 0.0077 - acc

1398/1398 [==============================] - ETA: 4s - loss: 0.0278 - accuracy: 0.98 - ETA: 4s - loss: 0.0154 - accuracy: 0.99 - ETA: 4s - loss: 0.0421 - accuracy: 0.98 - ETA: 4s - loss: 0.0848 - accuracy: 0.98 - ETA: 4s - loss: 0.0709 - accuracy: 0.98 - ETA: 3s - loss: 0.0621 - accuracy: 0.98 - ETA: 3s - loss: 0.0685 - accuracy: 0.98 - ETA: 3s - loss: 0.0692 - accuracy: 0.98 - ETA: 3s - loss: 0.0748 - accuracy: 0.98 - ETA: 3s - loss: 0.0784 - accuracy: 0.98 - ETA: 3s - loss: 0.0840 - accuracy: 0.98 - ETA: 2s - loss: 0.0845 - accuracy: 0.98 - ETA: 2s - loss: 0.0800 - accuracy: 0.98 - ETA: 2s - loss: 0.0756 - accuracy: 0.98 - ETA: 2s - loss: 0.0721 - accuracy: 0.98 - ETA: 2s - loss: 0.0685 - accuracy: 0.98 - ETA: 1s - loss: 0.0655 - accuracy: 0.98 - ETA: 1s - loss: 0.0627 - accuracy: 0.98 - ETA: 1s - loss: 0.0744 - accuracy: 0.98 - ETA: 1s - loss: 0.0713 - accuracy: 0.98 - ETA: 1s - loss: 0.0713 - accuracy: 0.98 - ETA: 1s - loss: 0.0693 - accuracy: 0.98 - ETA: 0s - loss: 0.0672 - accura

1398/1398 [==============================] - ETA: 2s - loss: 0.0069 - accuracy: 1.00 - ETA: 2s - loss: 0.0035 - accuracy: 1.00 - ETA: 2s - loss: 0.0024 - accuracy: 1.00 - ETA: 2s - loss: 0.0031 - accuracy: 1.00 - ETA: 1s - loss: 0.0026 - accuracy: 1.00 - ETA: 1s - loss: 0.0021 - accuracy: 1.00 - ETA: 1s - loss: 0.0019 - accuracy: 1.00 - ETA: 1s - loss: 0.0024 - accuracy: 1.00 - ETA: 1s - loss: 0.0032 - accuracy: 0.99 - ETA: 0s - loss: 0.0029 - accuracy: 0.99 - ETA: 0s - loss: 0.0038 - accuracy: 0.99 - ETA: 0s - loss: 0.0035 - accuracy: 0.99 - ETA: 0s - loss: 0.0033 - accuracy: 0.99 - 3s 2ms/step - loss: 0.0031 - accuracy: 0.9986
Epoch 5/10
1398/1398 [==============================] - ETA: 2s - loss: 0.0112 - accuracy: 0.99 - ETA: 2s - loss: 0.0069 - accuracy: 0.99 - ETA: 2s - loss: 0.0047 - accuracy: 0.99 - ETA: 2s - loss: 0.0035 - accuracy: 0.99 - ETA: 2s - loss: 0.0029 - accuracy: 0.99 - ETA: 1s - loss: 0.0024 - accuracy: 0.99 - ETA: 1s - loss: 0.0021 - accuracy: 0.99 - ETA: 1s - los